In [1]:
import numpy as np
import pandas as pd

import xgboost as xgb
from sklearn import preprocessing
from sklearn.model_selection import StratifiedKFold
from sklearn.model_selection import KFold
from sklearn.metrics import log_loss
import optuna

from tqdm import tqdm
import matplotlib.pyplot as plt
import seaborn as sns
import pickle
import os
import warnings
warnings.filterwarnings('ignore')

# Configuration

In [2]:
ROOT = ".."
INPUT = "input"
LISH_MOA = "lish-moa"
NUM_FOLD = 5
NUM_OPTUNA_TRIAL = 50

# Read data

In [3]:
train = pd.read_csv(os.path.join(ROOT, INPUT, LISH_MOA, "train_features.csv"))
test = pd.read_csv(os.path.join(ROOT, INPUT, LISH_MOA, "test_features.csv"))
train_targets_scored = pd.read_csv(os.path.join(ROOT, INPUT, LISH_MOA, "train_targets_scored.csv"))
train_targets_nonscored = pd.read_csv(os.path.join(ROOT, INPUT, LISH_MOA, "train_targets_nonscored.csv"))
sub = pd.read_csv(os.path.join(ROOT, INPUT, LISH_MOA, "sample_submission.csv"))

In [4]:
train_targets_scored.columns

Index(['sig_id', '5-alpha_reductase_inhibitor', '11-beta-hsd1_inhibitor',
       'acat_inhibitor', 'acetylcholine_receptor_agonist',
       'acetylcholine_receptor_antagonist', 'acetylcholinesterase_inhibitor',
       'adenosine_receptor_agonist', 'adenosine_receptor_antagonist',
       'adenylyl_cyclase_activator',
       ...
       'tropomyosin_receptor_kinase_inhibitor', 'trpv_agonist',
       'trpv_antagonist', 'tubulin_inhibitor', 'tyrosine_kinase_inhibitor',
       'ubiquitin_specific_protease_inhibitor', 'vegfr_inhibitor', 'vitamin_b',
       'vitamin_d_receptor_agonist', 'wnt_inhibitor'],
      dtype='object', length=207)

In [5]:
for col in train_targets_scored.columns:
    if col != 'sig_id':
        c = train_targets_scored[col].value_counts()
        if c[1] <= NUM_FOLD:
            print(col)

atp-sensitive_potassium_channel_antagonist
erbb2_inhibitor


## train_features.csv

In [6]:
print(train.shape)

(23814, 876)


In [7]:
train.head()

sig_id cp_type  cp_time cp_dose     g-0     g-1     g-2     g-3  \
0  id_000644bb2  trt_cp       24      D1  1.0620  0.5577 -0.2479 -0.6208   
1  id_000779bfc  trt_cp       72      D1  0.0743  0.4087  0.2991  0.0604   
2  id_000a6266a  trt_cp       48      D1  0.6280  0.5817  1.5540 -0.0764   
3  id_0015fd391  trt_cp       48      D1 -0.5138 -0.2491 -0.2656  0.5288   
4  id_001626bd3  trt_cp       72      D2 -0.3254 -0.4009  0.9700  0.6919   

      g-4     g-5  ...    c-90    c-91    c-92    c-93    c-94    c-95  \
0 -0.1944 -1.0120  ...  0.2862  0.2584  0.8076  0.5523 -0.1912  0.6584   
1  1.0190  0.5207  ... -0.4265  0.7543  0.4708  0.0230  0.2957  0.4899   
2 -0.0323  1.2390  ... -0.7250 -0.6297  0.6103  0.0223 -1.3240 -0.3174   
3  4.0620 -0.8095  ... -2.0990 -0.6441 -5.6300 -1.3780 -0.8632 -1.2880   
4  1.4180 -0.8244  ...  0.0042  0.0048  0.6670  1.0690  0.5523 -0.3031   

     c-96    c-97    c-98    c-99  
0 -0.3981  0.2139  0.3801  0.4176  
1  0.1522  0.1241  0.6077  0.7371  
2 -0.6417 -0.2187 -1.4080  0.6931  
3 -1.6210 -0.8784 -0.3876 -0.8154  
4  0.1094  0.2885 -0.3786  0.7125  

[5 rows x 876 columns]

## train_targets_socred.csv

In [8]:
print(train_targets_scored.shape)

(23814, 207)


In [9]:
train_targets_scored.head()

sig_id  5-alpha_reductase_inhibitor  11-beta-hsd1_inhibitor  \
0  id_000644bb2                            0                       0   
1  id_000779bfc                            0                       0   
2  id_000a6266a                            0                       0   
3  id_0015fd391                            0                       0   
4  id_001626bd3                            0                       0   

   acat_inhibitor  acetylcholine_receptor_agonist  \
0               0                               0   
1               0                               0   
2               0                               0   
3               0                               0   
4               0                               0   

   acetylcholine_receptor_antagonist  acetylcholinesterase_inhibitor  \
0                                  0                               0   
1                                  0                               0   
2                                  0                               0   
3                                  0                               0   
4                                  0                               0   

   adenosine_receptor_agonist  adenosine_receptor_antagonist  \
0                           0                              0   
1                           0                              0   
2                           0                              0   
3                           0                              0   
4                           0                              0   

   adenylyl_cyclase_activator  ...  tropomyosin_receptor_kinase_inhibitor  \
0                           0  ...                                      0   
1                           0  ...                                      0   
2                           0  ...                                      0   
3                           0  ...                                      0   
4                           0  ...                                      0   

   trpv_agonist  trpv_antagonist  tubulin_inhibitor  \
0             0                0                  0   
1             0                0                  0   
2             0                0                  0   
3             0                0                  0   
4             0                0                  0   

   tyrosine_kinase_inhibitor  ubiquitin_specific_protease_inhibitor  \
0                          0                                      0   
1                          0                                      0   
2                          0                                      0   
3                          0                                      0   
4                          0                                      0   

   vegfr_inhibitor  vitamin_b  vitamin_d_receptor_agonist  wnt_inhibitor  
0                0          0                           0              0  
1                0          0                           0              0  
2                0          0                           0              0  
3                0          0                           0              0  
4                0          0                           0              0  

[5 rows x 207 columns]

## test_features.csv

In [10]:
print(test.shape)

(3982, 876)


In [11]:
test.head()

sig_id      cp_type  cp_time cp_dose     g-0     g-1     g-2     g-3  \
0  id_0004d9e33       trt_cp       24      D1 -0.5458  0.1306 -0.5135  0.4408   
1  id_001897cda       trt_cp       72      D1 -0.1829  0.2320  1.2080 -0.4522   
2  id_002429b5b  ctl_vehicle       24      D1  0.1852 -0.1404 -0.3911  0.1310   
3  id_00276f245       trt_cp       24      D2  0.4828  0.1955  0.3825  0.4244   
4  id_0027f1083       trt_cp       48      D1 -0.3979 -1.2680  1.9130  0.2057   

      g-4     g-5  ...    c-90    c-91    c-92    c-93    c-94    c-95  \
0  1.5500 -0.1644  ...  0.0981  0.7978 -0.1430 -0.2067 -0.2303 -0.1193   
1 -0.3652 -0.3319  ... -0.1190 -0.1852 -1.0310 -1.3670 -0.3690 -0.5382   
2 -1.4380  0.2455  ... -0.2261  0.3370 -1.3840  0.8604 -1.9530 -1.0140   
3 -0.5855 -1.2020  ...  0.1260  0.1570 -0.1784 -1.1200 -0.4325 -0.9005   
4 -0.5864 -0.0166  ...  0.4965  0.7578 -0.1580  1.0510  0.5742  1.0900   

     c-96    c-97    c-98    c-99  
0  0.0210 -0.0502  0.1510 -0.7750  
1  0.0359 -0.4764 -1.3810 -0.7300  
2  0.8662  1.0160  0.4924 -0.1942  
3  0.8131 -0.1305  0.5645 -0.5809  
4 -0.2962 -0.5313  0.9931  1.8380  

[5 rows x 876 columns]

## train_targets_nonscored.csv (not use)

In [12]:
print(train_targets_nonscored.shape)

(23814, 403)


In [13]:
train_targets_nonscored.head()

sig_id  abc_transporter_expression_enhancer  abl_inhibitor  \
0  id_000644bb2                                    0              0   
1  id_000779bfc                                    0              0   
2  id_000a6266a                                    0              0   
3  id_0015fd391                                    0              0   
4  id_001626bd3                                    0              0   

   ace_inhibitor  acetylcholine_release_enhancer  \
0              0                               0   
1              0                               0   
2              0                               0   
3              0                               0   
4              0                               0   

   adenosine_deaminase_inhibitor  adenosine_kinase_inhibitor  \
0                              0                           0   
1                              0                           0   
2                              0                           0   
3                              0                           0   
4                              0                           0   

   adenylyl_cyclase_inhibitor  age_inhibitor  alcohol_dehydrogenase_inhibitor  \
0                           0              0                                0   
1                           0              0                                0   
2                           0              0                                0   
3                           0              0                                0   
4                           0              0                                0   

   ...  ve-cadherin_antagonist  vesicular_monoamine_transporter_inhibitor  \
0  ...                       0                                          0   
1  ...                       0                                          0   
2  ...                       0                                          0   
3  ...                       0                                          0   
4  ...                       0                                          0   

   vitamin_k_antagonist  voltage-gated_calcium_channel_ligand  \
0                     0                                     0   
1                     0                                     0   
2                     0                                     0   
3                     0                                     0   
4                     0                                     0   

   voltage-gated_potassium_channel_activator  \
0                                          0   
1                                          0   
2                                          0   
3                                          0   
4                                          0   

   voltage-gated_sodium_channel_blocker  wdr5_mll_interaction_inhibitor  \
0                                     0                               0   
1                                     0                               0   
2                                     0                               0   
3                                     0                               0   
4                                     0                               0   

   wnt_agonist  xanthine_oxidase_inhibitor  xiap_inhibitor  
0            0                           0               0  
1            0                           0               0  
2            0                           0               0  
3            0                           0               0  
4            0                           0               0  

[5 rows x 403 columns]

## submission.csv

In [14]:
sub.head()

sig_id  5-alpha_reductase_inhibitor  11-beta-hsd1_inhibitor  \
0  id_0004d9e33                          0.5                     0.5   
1  id_001897cda                          0.5                     0.5   
2  id_002429b5b                          0.5                     0.5   
3  id_00276f245                          0.5                     0.5   
4  id_0027f1083                          0.5                     0.5   

   acat_inhibitor  acetylcholine_receptor_agonist  \
0             0.5                             0.5   
1             0.5                             0.5   
2             0.5                             0.5   
3             0.5                             0.5   
4             0.5                             0.5   

   acetylcholine_receptor_antagonist  acetylcholinesterase_inhibitor  \
0                                0.5                             0.5   
1                                0.5                             0.5   
2                                0.5                             0.5   
3                                0.5                             0.5   
4                                0.5                             0.5   

   adenosine_receptor_agonist  adenosine_receptor_antagonist  \
0                         0.5                            0.5   
1                         0.5                            0.5   
2                         0.5                            0.5   
3                         0.5                            0.5   
4                         0.5                            0.5   

   adenylyl_cyclase_activator  ...  tropomyosin_receptor_kinase_inhibitor  \
0                         0.5  ...                                    0.5   
1                         0.5  ...                                    0.5   
2                         0.5  ...                                    0.5   
3                         0.5  ...                                    0.5   
4                         0.5  ...                                    0.5   

   trpv_agonist  trpv_antagonist  tubulin_inhibitor  \
0           0.5              0.5                0.5   
1           0.5              0.5                0.5   
2           0.5              0.5                0.5   
3           0.5              0.5                0.5   
4           0.5              0.5                0.5   

   tyrosine_kinase_inhibitor  ubiquitin_specific_protease_inhibitor  \
0                        0.5                                    0.5   
1                        0.5                                    0.5   
2                        0.5                                    0.5   
3                        0.5                                    0.5   
4                        0.5                                    0.5   

   vegfr_inhibitor  vitamin_b  vitamin_d_receptor_agonist  wnt_inhibitor  
0              0.5        0.5                         0.5            0.5  
1              0.5        0.5                         0.5            0.5  
2              0.5        0.5                         0.5            0.5  
3              0.5        0.5                         0.5            0.5  
4              0.5        0.5                         0.5            0.5  

[5 rows x 207 columns]

# Preprocessing

## Label Encoding

In [15]:
def label_encoding(train: pd.DataFrame, test: pd.DataFrame, encode_cols):
    n_train = len(train)
    train = pd.concat([train, test], sort=False).reset_index(drop=True)
    for f in encode_cols:
        try:
            lbl = preprocessing.LabelEncoder()
            train[f] = lbl.fit_transform(list(train[f].values))
        except:
            print(f)
    test = train[n_train:].reset_index(drop=True)
    train = train[:n_train]
    return train, test

In [16]:
train.select_dtypes(include=['object']).columns

Index(['sig_id', 'cp_type', 'cp_dose'], dtype='object')

In [17]:
# train['cp_type'] = train['cp_type'].astype(str)
# train['cp_dose'] = train['cp_dose'].astype(str)
# test['cp_type'] = test['cp_type'].astype(str)
# test['cp_dose'] = test['cp_dose'].astype(str)

In [18]:
train, test = label_encoding(train, test, ['cp_type', 'cp_dose'])

In [19]:
train.head()

sig_id  cp_type  cp_time  cp_dose     g-0     g-1     g-2     g-3  \
0  id_000644bb2        1       24        0  1.0620  0.5577 -0.2479 -0.6208   
1  id_000779bfc        1       72        0  0.0743  0.4087  0.2991  0.0604   
2  id_000a6266a        1       48        0  0.6280  0.5817  1.5540 -0.0764   
3  id_0015fd391        1       48        0 -0.5138 -0.2491 -0.2656  0.5288   
4  id_001626bd3        1       72        1 -0.3254 -0.4009  0.9700  0.6919   

      g-4     g-5  ...    c-90    c-91    c-92    c-93    c-94    c-95  \
0 -0.1944 -1.0120  ...  0.2862  0.2584  0.8076  0.5523 -0.1912  0.6584   
1  1.0190  0.5207  ... -0.4265  0.7543  0.4708  0.0230  0.2957  0.4899   
2 -0.0323  1.2390  ... -0.7250 -0.6297  0.6103  0.0223 -1.3240 -0.3174   
3  4.0620 -0.8095  ... -2.0990 -0.6441 -5.6300 -1.3780 -0.8632 -1.2880   
4  1.4180 -0.8244  ...  0.0042  0.0048  0.6670  1.0690  0.5523 -0.3031   

     c-96    c-97    c-98    c-99  
0 -0.3981  0.2139  0.3801  0.4176  
1  0.1522  0.1241  0.6077  0.7371  
2 -0.6417 -0.2187 -1.4080  0.6931  
3 -1.6210 -0.8784 -0.3876 -0.8154  
4  0.1094  0.2885 -0.3786  0.7125  

[5 rows x 876 columns]

In [20]:
test.head()

sig_id  cp_type  cp_time  cp_dose     g-0     g-1     g-2     g-3  \
0  id_0004d9e33        1       24        0 -0.5458  0.1306 -0.5135  0.4408   
1  id_001897cda        1       72        0 -0.1829  0.2320  1.2080 -0.4522   
2  id_002429b5b        0       24        0  0.1852 -0.1404 -0.3911  0.1310   
3  id_00276f245        1       24        1  0.4828  0.1955  0.3825  0.4244   
4  id_0027f1083        1       48        0 -0.3979 -1.2680  1.9130  0.2057   

      g-4     g-5  ...    c-90    c-91    c-92    c-93    c-94    c-95  \
0  1.5500 -0.1644  ...  0.0981  0.7978 -0.1430 -0.2067 -0.2303 -0.1193   
1 -0.3652 -0.3319  ... -0.1190 -0.1852 -1.0310 -1.3670 -0.3690 -0.5382   
2 -1.4380  0.2455  ... -0.2261  0.3370 -1.3840  0.8604 -1.9530 -1.0140   
3 -0.5855 -1.2020  ...  0.1260  0.1570 -0.1784 -1.1200 -0.4325 -0.9005   
4 -0.5864 -0.0166  ...  0.4965  0.7578 -0.1580  1.0510  0.5742  1.0900   

     c-96    c-97    c-98    c-99  
0  0.0210 -0.0502  0.1510 -0.7750  
1  0.0359 -0.4764 -1.3810 -0.7300  
2  0.8662  1.0160  0.4924 -0.1942  
3  0.8131 -0.1305  0.5645 -0.5809  
4 -0.2962 -0.5313  0.9931  1.8380  

[5 rows x 876 columns]

# Cross Validation by using Optuna

In [21]:
def xgboost_cv(data, targets, target_col, cv):
    def objective(trial):
        param = {
            'objective': 'binary:logistic',
            'n_estimators': 1000,
            'learning_rate': 0.1,
            'subsample': trial.suggest_discrete_uniform('subsample', 0.6, 0.95, 0.05),
            'colsample_bytree': trial.suggest_discrete_uniform('colsample_bytree', 0.6, 0.95, 0.05),
            'max_depth':  trial.suggest_int('max_depth', 3, 9),
            'gamma': trial.suggest_loguniform('gamma', 1e-8, 1.0),
            'min_child_weight': trial.suggest_loguniform('min_child_weight', 0.1, 10.0),
            'tree_method': 'gpu_hist'
        }
        
        df_x = data.drop(["sig_id"], axis=1)
        df_y = targets[target_col]
        score_logloss = 0.
        
        # cross validation
        for fold_id, (train_index, valid_index) in enumerate(tqdm(cv.split(df_x, df_y))):
            X_train = df_x.loc[train_index, :]
            y_train = df_y[train_index]
            X_valid = df_x.loc[valid_index, :]
            y_valid = df_y.loc[valid_index]
            
            model = xgb.XGBClassifier(**param)
            model.fit(X_train, y_train, eval_set=[(X_valid, y_valid)],
                      eval_metric='logloss', verbose=False, early_stopping_rounds=50)
            y_pred = model.predict_proba(X_valid)
            score_logloss += log_loss(y_valid, y_pred, labels=[0, 1])

        score_logloss /= NUM_FOLD
        return score_logloss
    return objective
        

In [22]:
cv = StratifiedKFold(n_splits=NUM_FOLD, shuffle=True, random_state=0)

In [23]:
skip_cols = ["atp-sensitive_potassium_channel_antagonist", "erbb2_inhibitor"]

In [24]:
for target_col in tqdm(train_targets_scored.columns):
    if (target_col != "sig_id") and not (target_col in skip_cols):
        print('##################### CV START: {0} #####################'.format(target_col))
        
        # optimize by optuna
        study = optuna.create_study()
        study.optimize(xgboost_cv(train, train_targets_scored, target_col, cv), n_trials=NUM_OPTUNA_TRIAL)
        
        # save optuna log
        df_trial = study.trials_dataframe()
        df_trial.to_pickle(os.path.join('report', 'OptunaLog_'+target_col+'.pkl'))

        # save best params found by CV
        bestparam_filename = 'BestParamsSelectedByCV_'+target_col+'.pkl'
        with open(os.path.join('result', 'best_param_cv', bestparam_filename), 'wb') as f:
            pickle.dump(study.best_params, f)


  0%|                                                                                          | 0/207 [00:00<?, ?it/s]

##################### CV START: 5-alpha_reductase_inhibitor #####################



0it [00:00, ?it/s]
1it [00:02,  2.42s/it]
2it [00:04,  2.36s/it]
3it [00:06,  2.32s/it]
4it [00:09,  2.28s/it]
5it [00:11,  2.25s/it]
[I 2020-10-12 13:36:33,377] Finished trial#0 with value: 0.005527013307752131 with parameters: {'subsample': 0.75, 'colsample_bytree': 0.9, 'max_depth': 5, 'gamma': 5.1099058126336026e-05, 'min_child_weight': 0.1830384462907805}. Best is trial#0 with value: 0.005527013307752131.

0it [00:00, ?it/s]
1it [00:02,  2.26s/it]
2it [00:04,  2.25s/it]
3it [00:06,  2.24s/it]
4it [00:08,  2.24s/it]
5it [00:11,  2.23s/it]
[I 2020-10-12 13:36:44,667] Finished trial#1 with value: 0.0055930388856715064 with parameters: {'subsample': 0.7, 'colsample_bytree': 0.8, 'max_depth': 8, 'gamma': 0.07254853393257188, 'min_child_weight': 0.1359134036696732}. Best is trial#0 with value: 0.005527013307752131.

0it [00:00, ?it/s]
1it [00:02,  2.14s/it]
2it [00:04,  2.16s/it]
3it [00:06,  2.19s/it]
4it [00:08,  2.17s/it]
5it [00:10,  2.17s/it]
[I 2020-10-12 13:36:55,624] Finished t

##################### CV START: 11-beta-hsd1_inhibitor #####################



0it [00:00, ?it/s]
1it [00:02,  2.14s/it]
2it [00:04,  2.12s/it]
3it [00:06,  2.10s/it]
4it [00:08,  2.09s/it]
5it [00:10,  2.10s/it]
[I 2020-10-12 13:45:57,285] Finished trial#0 with value: 0.006310316737796029 with parameters: {'subsample': 0.9, 'colsample_bytree': 0.75, 'max_depth': 4, 'gamma': 0.0008874793568235074, 'min_child_weight': 1.2664223603487044}. Best is trial#0 with value: 0.006310316737796029.

0it [00:00, ?it/s]
1it [00:02,  2.22s/it]
2it [00:04,  2.21s/it]
3it [00:06,  2.20s/it]
4it [00:08,  2.20s/it]
5it [00:11,  2.22s/it]
[I 2020-10-12 13:46:08,498] Finished trial#1 with value: 0.006140058792137635 with parameters: {'subsample': 0.8, 'colsample_bytree': 0.95, 'max_depth': 6, 'gamma': 0.06495499638405365, 'min_child_weight': 0.29290375790936507}. Best is trial#1 with value: 0.006140058792137635.

0it [00:00, ?it/s]
1it [00:02,  2.22s/it]
2it [00:04,  2.15s/it]
3it [00:06,  2.10s/it]
4it [00:08,  2.08s/it]
5it [00:10,  2.09s/it]
[I 2020-10-12 13:46:19,075] Finished t

...


0it [00:00, ?it/s]
1it [00:02,  2.09s/it]
2it [00:04,  2.09s/it]
3it [00:06,  2.15s/it]
4it [00:08,  2.09s/it]
5it [00:10,  2.10s/it]
[I 2020-10-13 21:49:24,444] Finished trial#0 with value: 0.00851304524036745 with parameters: {'subsample': 0.6, 'colsample_bytree': 0.65, 'max_depth': 5, 'gamma': 1.29613713886907e-05, 'min_child_weight': 1.3157948879175234}. Best is trial#0 with value: 0.00851304524036745.

0it [00:00, ?it/s]
1it [00:02,  2.08s/it]
2it [00:04,  2.11s/it]
3it [00:06,  2.11s/it]
4it [00:08,  2.10s/it]
5it [00:10,  2.09s/it]
[I 2020-10-13 21:49:35,049] Finished trial#1 with value: 0.008326653302253479 with parameters: {'subsample': 0.85, 'colsample_bytree': 0.8, 'max_depth': 4, 'gamma': 0.06910074565187382, 'min_child_weight': 1.2633316681948488}. Best is trial#1 with value: 0.008326653302253479.

0it [00:00, ?it/s]
1it [00:02,  2.37s/it]
2it [00:04,  2.35s/it]
3it [00:07,  2.38s/it]
4it [00:09,  2.37s/it]
5it [00:11,  2.37s/it]
[I 2020-10-13 21:49:47,036] Finished trial

##################### CV START: vitamin_d_receptor_agonist #####################



0it [00:00, ?it/s]
1it [00:02,  2.13s/it]
2it [00:04,  2.33s/it]
3it [00:07,  2.35s/it]
4it [00:09,  2.35s/it]
5it [00:12,  2.48s/it]
[I 2020-10-13 21:58:16,304] Finished trial#0 with value: 0.006014524157039298 with parameters: {'subsample': 0.6, 'colsample_bytree': 0.6, 'max_depth': 7, 'gamma': 0.26631447593931723, 'min_child_weight': 6.020178143420728}. Best is trial#0 with value: 0.006014524157039298.

0it [00:00, ?it/s]
1it [00:02,  2.42s/it]
2it [00:05,  2.50s/it]
3it [00:07,  2.54s/it]
4it [00:10,  2.50s/it]
5it [00:12,  2.58s/it]
[I 2020-10-13 21:58:29,379] Finished trial#1 with value: 0.005775078688370079 with parameters: {'subsample': 0.8, 'colsample_bytree': 0.7, 'max_depth': 3, 'gamma': 0.0014771327873351473, 'min_child_weight': 5.943008325545437}. Best is trial#1 with value: 0.005775078688370079.

0it [00:00, ?it/s]
1it [00:02,  2.15s/it]
2it [00:04,  2.19s/it]
3it [00:06,  2.17s/it]
4it [00:08,  2.15s/it]
5it [00:10,  2.19s/it]
[I 2020-10-13 21:58:40,463] Finished trial#

##################### CV START: wnt_inhibitor #####################



0it [00:00, ?it/s]
1it [00:02,  2.00s/it]
2it [00:04,  2.04s/it]
3it [00:06,  2.11s/it]
4it [00:08,  2.12s/it]
5it [00:10,  2.11s/it]
[I 2020-10-13 22:08:41,245] Finished trial#0 with value: 0.00955296599235263 with parameters: {'subsample': 0.7, 'colsample_bytree': 0.95, 'max_depth': 7, 'gamma': 1.7318924900184204e-05, 'min_child_weight': 5.399602864090778}. Best is trial#0 with value: 0.00955296599235263.

0it [00:00, ?it/s]
1it [00:02,  2.26s/it]
2it [00:04,  2.26s/it]
3it [00:06,  2.26s/it]
4it [00:09,  2.25s/it]
5it [00:11,  2.23s/it]
[I 2020-10-13 22:08:52,541] Finished trial#1 with value: 0.009598693768014865 with parameters: {'subsample': 0.7, 'colsample_bytree': 0.9, 'max_depth': 6, 'gamma': 3.4399012055335806e-07, 'min_child_weight': 0.3281671860352421}. Best is trial#0 with value: 0.00955296599235263.

0it [00:00, ?it/s]
1it [00:02,  2.09s/it]
2it [00:04,  2.13s/it]
3it [00:06,  2.18s/it]
4it [00:08,  2.21s/it]
5it [00:11,  2.20s/it]
[I 2020-10-13 22:09:03,681] Finished tri

# Train & Predict by best model

In [25]:
submission = sub.copy()

In [26]:
def xgboost_bestparam(data_train, targets_train, data_test, target_col, best_params, submission):
    print('##################### TraingByBestParam START: {0} #####################'.format(target_col))
    
    # prepare data set
    X_train = data_train.drop(["sig_id"], axis=1)
    y_train = targets_train[target_col]
    X_test = data_test.drop(["sig_id"], axis=1)
    
    # train XGBoost by using best_params
    model = xgb.XGBClassifier(**best_params)
    model.fit(X_train, y_train, eval_metric='logloss')
    
    # predict for test
    submission[target_col] = model.predict_proba(X_test)[:, 1]
    
    # save model for test
    modelfile = 'BestModel4test_'+target_col+'.pkl'
    with open(os.path.join('result', 'best_model', modelfile), 'wb') as f:
        pickle.dump(model, f)
    

In [27]:
for target_col in tqdm(train_targets_scored.columns):
    if target_col != "sig_id" and not (target_col in skip_cols):
        # read best param selected by CV
        bestparam_filename = 'BestParamsSelectedByCV_'+target_col+'.pkl'
        with open(os.path.join('result', 'best_param_cv', bestparam_filename), 'rb') as f:
            best_params = pickle.load(f)
            
        best_params['objective'] = 'binary:logistic'
        best_params['n_estimators'] = 1000
        best_params['learning_rate'] = 0.1
        best_params['tree_method'] = 'gpu_hist'
        
        xgboost_bestparam(train, train_targets_scored, test, target_col, best_params, submission)
    elif target_col in skip_cols:
        submission[target_col] = 0

  0%|                                                                                          | 0/207 [00:00<?, ?it/s]

##################### TraingByBestParam START: 5-alpha_reductase_inhibitor #####################


  1%|▊                                                                                 | 2/207 [00:07<13:25,  3.93s/it]

##################### TraingByBestParam START: 11-beta-hsd1_inhibitor #####################


  1%|█▏                                                                                | 3/207 [00:16<17:55,  5.27s/it]

...

 99%|███████████████████████████████████████████████████████████████████████████████▏| 205/207 [29:49<00:17,  8.87s/it]

##################### TraingByBestParam START: vitamin_d_receptor_agonist #####################


100%|███████████████████████████████████████████████████████████████████████████████▌| 206/207 [29:57<00:08,  8.55s/it]

##################### TraingByBestParam START: wnt_inhibitor #####################


100%|████████████████████████████████████████████████████████████████████████████████| 207/207 [30:05<00:00,  8.72s/it]


In [28]:
submission.to_csv('submission.csv', index=False)